In [25]:
import pandas as pd
import numpy as np
import json
from pathlib import Path  
from ast import literal_eval

In [26]:
pd.set_option('display.max_rows', None)

In [60]:
with open("tools/state_codes.json", 'r') as f:
    state_codes = json.load(f)

with open("tools/countyfy.json", 'r') as f:
    county_dict_raw = json.load(f)

county_dict = {}
for key in county_dict_raw:
    county_dict[literal_eval(key.replace('~', '\\\''))] = county_dict_raw[key]

def decountify(s):
    if (s == "Carson City"):
        return
        
    return " ".join([i for i in s.split() if i.lower() not in ["county", "parish", "municipality", "borough", "town", "city"]])

In [61]:
col_data = "datasets/cost-of-living-database.xlsx"
MIN_COUNTY_SIZE = 25000

In [62]:
col_food = pd.read_excel(col_data, sheet_name="Food Costs")
col_rent = pd.read_excel(col_data, sheet_name="Housing Costs - Rent")

col_rent_temp = col_rent
col_rent_temp.columns = col_rent_temp.iloc[1]
col_rent_temp = col_rent_temp.drop([0,1])
col_rent_temp = col_rent_temp[(col_rent_temp["numadults"] == 1) & 
                              (col_rent_temp["numkids"] == 0)]
                              #(col_rent_temp["stateAbbrev"].isin(["CT", "DC", "ME", "NH", "RI", "VA"]))]
col_rent_temp = col_rent_temp[["stateAbbrev", "countyortownName", "expense.rent", "countyortownpop"]]
# col_rent_temp[]

In [63]:
display(col_rent_temp)

1     stateAbbrev                      countyortownName  expense.rent  \
2              AL                        Autauga County   7145.714278   
17             AL                        Baldwin County   8069.714278   
32             AL                        Barbour County   4829.714278   
47             AL                           Bibb County   7949.714278   
62             AL                         Blount County   7949.714278   
77             AL                        Bullock County   4805.714278   
92             AL                         Butler County   4505.714278   
107            AL                        Calhoun County   4949.714278   
122            AL                       Chambers County   5741.714278   
137            AL                       Cherokee County   4493.714278   
152            AL                        Chilton County   5381.714278   
167            AL                        Choctaw County   4805.714278   
182            AL                         Clarke County   5249.714278   
197            AL                           Clay County   5381.714278   
212            AL                       Cleburne County   4493.714278   
227            AL                         Coffee County   5489.714278   
242            AL                        Colbert County   5201.714278   
257            AL                        Conecuh County   4529.714278   
272            AL                          Coosa County   4925.714278   
287            AL                      Covington County   4649.714278   
302            AL                       Crenshaw County   4493.714278   
317            AL                        Cullman County   5213.714278   
332            AL                           Dale County   4805.714278   
347            AL                         Dallas County   5081.714278   
362            AL                         DeKalb County   4637.714278   
377            AL                         Elmore County   7145.714278   
392            AL                       Escambia County   5381.714278   
407            AL                         Etowah County   4793.714278   
422            AL                        Fayette County   5381.714278   
437            AL                       Franklin County   5309.714278   
452            AL                         Geneva County   5021.714278   
467            AL                         Greene County   5381.714278   
482            AL                           Hale County   7253.714278   
497            AL                          Henry County   5381.714278   
512            AL                        Houston County   5021.714278   
527            AL                        Jackson County   5705.714278   
542            AL                      Jefferson County   7949.714278   
557            AL                          Lamar County   5345.714278   
572            AL                     Lauderdale County   5201.714278   
587            AL                       Lawrence County   5129.714278   
602            AL                            Lee County   6317.714278   
617            AL                      Limestone County   7013.714278   
632            AL                        Lowndes County   7145.714278   
647            AL                          Macon County   4493.714278   
662            AL                        Madison County   7013.714278   
677            AL                        Marengo County   5261.714278   
692            AL                         Marion County   4493.714278   
707            AL                       Marshall County   4625.714278   
722            AL                         Mobile County   6965.714278   
737            AL                         Monroe County   5381.714278   
752            AL                     Montgomery County   7145.714278   
767            AL                         Morgan County   5129.714278   
782            AL                          Perry County   5381.714278   
797            AL                        Pickens County   

In [64]:
col_rent_temp_test = col_rent_temp


In [65]:
countied = {}
mfd = []

In [66]:
def combineRows(row):
#     print(row.name)
#     name = " ".join(row[1].split()[:-1])
    name = decountify(row[1])
#     print(name)
    if (name, row[0]) not in county_dict:
#         print((name, row[0]))
        return
    
    if county_dict[(name, row[0])] not in countied:
        countied[county_dict[(name, row[0])]] = {"stateAbbrev": [row[0]], 
                                                 "countyortownName": [county_dict[(name, row[0])]], 
                                                 "expense.rent": [row[2]], 
                                                 "countyortownpop": [0]}
    mfd.append(row.name)
        
    countied[county_dict[(name, row[0])]]["countyortownpop"][0] += row[3]
    return countied

col_rent_temp_test.apply(combineRows, axis=1)
# col_rent_temp_test

2                                                     None
17                                                    None
32                                                    None
47                                                    None
62                                                    None
77                                                    None
92                                                    None
107                                                   None
122                                                   None
137                                                   None
152                                                   None
167                                                   None
182                                                   None
197                                                   None
212                                                   None
227                                                   None
242                                                   No

In [67]:
countied

{'Fairfield County': {'stateAbbrev': ['CT'],
  'countyortownName': ['Fairfield County'],
  'expense.rent': [13829.7142781554],
  'countyortownpop': [916829]},
 'Hartford County': {'stateAbbrev': ['CT'],
  'countyortownName': ['Hartford County'],
  'expense.rent': [10313.7142781554],
  'countyortownpop': [894014]},
 'Litchfield County': {'stateAbbrev': ['CT'],
  'countyortownName': ['Litchfield County'],
  'expense.rent': [9485.71427815536],
  'countyortownpop': [189927]},
 'Middlesex County': {'stateAbbrev': ['CT'],
  'countyortownName': ['Middlesex County'],
  'expense.rent': [10313.7142781554],
  'countyortownpop': [1668761]},
 'New Haven County': {'stateAbbrev': ['CT'],
  'countyortownName': ['New Haven County'],
  'expense.rent': [12125.7142781554],
  'countyortownpop': [862477]},
 'New London County': {'stateAbbrev': ['CT'],
  'countyortownName': ['New London County'],
  'expense.rent': [9569.71427815536],
  'countyortownpop': [274055]},
 'Tolland County': {'stateAbbrev': ['CT'],


In [68]:
mfd

[4622,
 4637,
 4652,
 4667,
 4682,
 4697,
 4712,
 4727,
 4742,
 4757,
 4772,
 4787,
 4802,
 4817,
 4832,
 4847,
 4862,
 4877,
 4892,
 4907,
 4922,
 4937,
 4952,
 4967,
 4982,
 4997,
 5012,
 5027,
 5042,
 5057,
 5072,
 5087,
 5102,
 5117,
 5132,
 5147,
 5162,
 5177,
 5192,
 5207,
 5222,
 5237,
 5252,
 5267,
 5282,
 5297,
 5312,
 5327,
 5342,
 5357,
 5372,
 5387,
 5402,
 5417,
 5432,
 5447,
 5462,
 5477,
 5492,
 5507,
 5522,
 5537,
 5552,
 5567,
 5582,
 5597,
 5612,
 5627,
 5642,
 5657,
 5672,
 5687,
 5702,
 5717,
 5732,
 5747,
 5762,
 5777,
 5792,
 5807,
 5822,
 5837,
 5852,
 5867,
 5882,
 5897,
 5912,
 5927,
 5942,
 5957,
 5972,
 5987,
 6002,
 6017,
 6032,
 6047,
 6062,
 6077,
 6092,
 6107,
 6122,
 6137,
 6152,
 6167,
 6182,
 6197,
 6212,
 6227,
 6242,
 6257,
 6272,
 6287,
 6302,
 6317,
 6332,
 6347,
 6362,
 6377,
 6392,
 6407,
 6422,
 6437,
 6452,
 6467,
 6482,
 6497,
 6512,
 6527,
 6542,
 6557,
 6572,
 6587,
 6602,
 6617,
 6632,
 6647,
 6662,
 6677,
 6692,
 6707,
 6722,
 6737,
 6752,

In [69]:
for r in mfd:
    col_rent_temp = col_rent_temp.drop(r)

In [70]:
col_rent_temp

1     stateAbbrev                      countyortownName  expense.rent  \
2              AL                        Autauga County   7145.714278   
17             AL                        Baldwin County   8069.714278   
32             AL                        Barbour County   4829.714278   
47             AL                           Bibb County   7949.714278   
62             AL                         Blount County   7949.714278   
77             AL                        Bullock County   4805.714278   
92             AL                         Butler County   4505.714278   
107            AL                        Calhoun County   4949.714278   
122            AL                       Chambers County   5741.714278   
137            AL                       Cherokee County   4493.714278   
152            AL                        Chilton County   5381.714278   
167            AL                        Choctaw County   4805.714278   
182            AL                         Clarke County   5249.714278   
197            AL                           Clay County   5381.714278   
212            AL                       Cleburne County   4493.714278   
227            AL                         Coffee County   5489.714278   
242            AL                        Colbert County   5201.714278   
257            AL                        Conecuh County   4529.714278   
272            AL                          Coosa County   4925.714278   
287            AL                      Covington County   4649.714278   
302            AL                       Crenshaw County   4493.714278   
317            AL                        Cullman County   5213.714278   
332            AL                           Dale County   4805.714278   
347            AL                         Dallas County   5081.714278   
362            AL                         DeKalb County   4637.714278   
377            AL                         Elmore County   7145.714278   
392            AL                       Escambia County   5381.714278   
407            AL                         Etowah County   4793.714278   
422            AL                        Fayette County   5381.714278   
437            AL                       Franklin County   5309.714278   
452            AL                         Geneva County   5021.714278   
467            AL                         Greene County   5381.714278   
482            AL                           Hale County   7253.714278   
497            AL                          Henry County   5381.714278   
512            AL                        Houston County   5021.714278   
527            AL                        Jackson County   5705.714278   
542            AL                      Jefferson County   7949.714278   
557            AL                          Lamar County   5345.714278   
572            AL                     Lauderdale County   5201.714278   
587            AL                       Lawrence County   5129.714278   
602            AL                            Lee County   6317.714278   
617            AL                      Limestone County   7013.714278   
632            AL                        Lowndes County   7145.714278   
647            AL                          Macon County   4493.714278   
662            AL                        Madison County   7013.714278   
677            AL                        Marengo County   5261.714278   
692            AL                         Marion County   4493.714278   
707            AL                       Marshall County   4625.714278   
722            AL                         Mobile County   6965.714278   
737            AL                         Monroe County   5381.714278   
752            AL                     Montgomery County   7145.714278   
767            AL                         Morgan County   5129.714278   
782            AL                          Perry County   5381.714278   
797            AL                        Pickens County   

In [71]:
countied

{'Fairfield County': {'stateAbbrev': ['CT'],
  'countyortownName': ['Fairfield County'],
  'expense.rent': [13829.7142781554],
  'countyortownpop': [916829]},
 'Hartford County': {'stateAbbrev': ['CT'],
  'countyortownName': ['Hartford County'],
  'expense.rent': [10313.7142781554],
  'countyortownpop': [894014]},
 'Litchfield County': {'stateAbbrev': ['CT'],
  'countyortownName': ['Litchfield County'],
  'expense.rent': [9485.71427815536],
  'countyortownpop': [189927]},
 'Middlesex County': {'stateAbbrev': ['CT'],
  'countyortownName': ['Middlesex County'],
  'expense.rent': [10313.7142781554],
  'countyortownpop': [1668761]},
 'New Haven County': {'stateAbbrev': ['CT'],
  'countyortownName': ['New Haven County'],
  'expense.rent': [12125.7142781554],
  'countyortownpop': [862477]},
 'New London County': {'stateAbbrev': ['CT'],
  'countyortownName': ['New London County'],
  'expense.rent': [9569.71427815536],
  'countyortownpop': [274055]},
 'Tolland County': {'stateAbbrev': ['CT'],


In [72]:
for new_county in countied:
    print(pd.DataFrame(countied[new_county]))
    col_rent_temp = pd.concat([col_rent_temp, pd.DataFrame(countied[new_county])])

  stateAbbrev  countyortownName  expense.rent  countyortownpop
0          CT  Fairfield County  13829.714278           916829
  stateAbbrev countyortownName  expense.rent  countyortownpop
0          CT  Hartford County  10313.714278           894014
  stateAbbrev   countyortownName  expense.rent  countyortownpop
0          CT  Litchfield County   9485.714278           189927
  stateAbbrev  countyortownName  expense.rent  countyortownpop
0          CT  Middlesex County  10313.714278          1668761
  stateAbbrev  countyortownName  expense.rent  countyortownpop
0          CT  New Haven County  12125.714278           862477
  stateAbbrev   countyortownName  expense.rent  countyortownpop
0          CT  New London County   9569.714278           274055
  stateAbbrev countyortownName  expense.rent  countyortownpop
0          CT   Tolland County  10313.714278           152691
  stateAbbrev countyortownName  expense.rent  countyortownpop
0          CT   Windham County   8693.714278           1

In [73]:
col_rent_temp

stateAbbrev                      countyortownName  expense.rent  \
2              AL                        Autauga County   7145.714278   
17             AL                        Baldwin County   8069.714278   
32             AL                        Barbour County   4829.714278   
47             AL                           Bibb County   7949.714278   
62             AL                         Blount County   7949.714278   
77             AL                        Bullock County   4805.714278   
92             AL                         Butler County   4505.714278   
107            AL                        Calhoun County   4949.714278   
122            AL                       Chambers County   5741.714278   
137            AL                       Cherokee County   4493.714278   
152            AL                        Chilton County   5381.714278   
167            AL                        Choctaw County   4805.714278   
182            AL                         Clarke County   5249.714278   
197            AL                           Clay County   5381.714278   
212            AL                       Cleburne County   4493.714278   
227            AL                         Coffee County   5489.714278   
242            AL                        Colbert County   5201.714278   
257            AL                        Conecuh County   4529.714278   
272            AL                          Coosa County   4925.714278   
287            AL                      Covington County   4649.714278   
302            AL                       Crenshaw County   4493.714278   
317            AL                        Cullman County   5213.714278   
332            AL                           Dale County   4805.714278   
347            AL                         Dallas County   5081.714278   
362            AL                         DeKalb County   4637.714278   
377            AL                         Elmore County   7145.714278   
392            AL                       Escambia County   5381.714278   
407            AL                         Etowah County   4793.714278   
422            AL                        Fayette County   5381.714278   
437            AL                       Franklin County   5309.714278   
452            AL                         Geneva County   5021.714278   
467            AL                         Greene County   5381.714278   
482            AL                           Hale County   7253.714278   
497            AL                          Henry County   5381.714278   
512            AL                        Houston County   5021.714278   
527            AL                        Jackson County   5705.714278   
542            AL                      Jefferson County   7949.714278   
557            AL                          Lamar County   5345.714278   
572            AL                     Lauderdale County   5201.714278   
587            AL                       Lawrence County   5129.714278   
602            AL                            Lee County   6317.714278   
617            AL                      Limestone County   7013.714278   
632            AL                        Lowndes County   7145.714278   
647            AL                          Macon County   4493.714278   
662            AL                        Madison County   7013.714278   
677            AL                        Marengo County   5261.714278   
692            AL                         Marion County   4493.714278   
707            AL                       Marshall County   4625.714278   
722            AL                         Mobile County   6965.714278   
737            AL                         Monroe County   5381.714278   
752            AL                     Montgomery County   7145.714278   
767            AL                         Morgan County   5129.714278   
782            AL                          Perry County   5381.714278   
797            AL                        Pickens County   4565.7

In [74]:
col_rent = col_rent_temp.loc[col_rent_temp["countyortownpop"] >= MIN_COUNTY_SIZE].sort_values(['stateAbbrev', 'countyortownName'])#.reset_index().drop(columns=["index"])
col_rent = col_rent.rename(columns={"stateAbbrev": "state", "countyortownName": "county", "countyortownpop": "pop"})
col_rent

state                        county  expense.rent      pop
1037     AK        Anchorage Municipality  10853.714278   291826
1112     AK  Fairbanks North Star Borough  11093.714278    97581
1157     AK       Juneau City and Borough  12005.714278    31275
1172     AK       Kenai Peninsula Borough   9149.714278    55400
1247     AK     Matanuska-Susitna Borough   8573.714278    88995
2        AL                Autauga County   7145.714278    54571
17       AL                Baldwin County   8069.714278   182265
32       AL                Barbour County   4829.714278    27457
62       AL                 Blount County   7949.714278    57322
107      AL                Calhoun County   4949.714278   118572
122      AL               Chambers County   5741.714278    34215
137      AL               Cherokee County   4493.714278    25989
152      AL                Chilton County   5381.714278    43643
182      AL                 Clarke County   5249.714278    25833
227      AL                 Coffee County   5489.714278    49948
242      AL                Colbert County   5201.714278    54428
287      AL              Covington County   4649.714278    37765
317      AL                Cullman County   5213.714278    80406
332      AL                   Dale County   4805.714278    50251
347      AL                 Dallas County   5081.714278    43820
362      AL                 DeKalb County   4637.714278    71109
377      AL                 Elmore County   7145.714278    79303
392      AL               Escambia County   5381.714278    38319
407      AL                 Etowah County   4793.714278   104430
437      AL               Franklin County   5309.714278    31704
452      AL                 Geneva County   5021.714278    26790
512      AL                Houston County   5021.714278   101547
527      AL                Jackson County   5705.714278    53227
542      AL              Jefferson County   7949.714278   658466
572      AL             Lauderdale County   5201.714278    92709
587      AL               Lawrence County   5129.714278    34339
602      AL                    Lee County   6317.714278   140247
617      AL              Limestone County   7013.714278    82782
662      AL                Madison County   7013.714278   334811
692      AL                 Marion County   4493.714278    30776
707      AL               Marshall County   4625.714278    93019
722      AL                 Mobile County   6965.714278   412992
752      AL             Montgomery County   7145.714278   229363
767      AL                 Morgan County   5129.714278   119490
812      AL                   Pike County   5273.714278    32899
842      AL                Russell County   7361.714278    52947
872      AL                 Shelby County   7949.714278   195085
857      AL              St. Clair County   7949.714278    83593
902      AL              Talladega County   4889.714278    82291
917      AL             Tallapoosa County   5261.714278    41616
932      AL             Tuscaloosa County   7253.714278   194656
947      AL                 Walker County   4817.714278    67023
1697     AR                 Baxter County   5285.714278    41513
1712     AR                 Benton County   5825.714278   221339
1727     AR                  Boone County   4697.714278    36903
1772     AR                Carroll County   4781.714278    27446
1832     AR               Cleburne County   5141.714278    25970
1892     AR              Craighead County   6101.714278    96443
1907     AR               Crawford County   5141.714278    61948
1922     AR             Crittenden County   7697.714278    50902
1997     AR               Faulkner County   7217.714278   113237
2042     AR                Garland County   5837.714278    96024
2072     AR                 Greene County   5849.714278    42090
2102     AR             Hot Spring County   5273.714278    32923
2132     AR           Independence County   4685.714278    36647
2177     AR              Jefferson County

In [75]:
len(col_rent)

1593

In [76]:
col_rent

state                        county  expense.rent      pop
1037     AK        Anchorage Municipality  10853.714278   291826
1112     AK  Fairbanks North Star Borough  11093.714278    97581
1157     AK       Juneau City and Borough  12005.714278    31275
1172     AK       Kenai Peninsula Borough   9149.714278    55400
1247     AK     Matanuska-Susitna Borough   8573.714278    88995
2        AL                Autauga County   7145.714278    54571
17       AL                Baldwin County   8069.714278   182265
32       AL                Barbour County   4829.714278    27457
62       AL                 Blount County   7949.714278    57322
107      AL                Calhoun County   4949.714278   118572
122      AL               Chambers County   5741.714278    34215
137      AL               Cherokee County   4493.714278    25989
152      AL                Chilton County   5381.714278    43643
182      AL                 Clarke County   5249.714278    25833
227      AL                 Coffee County   5489.714278    49948
242      AL                Colbert County   5201.714278    54428
287      AL              Covington County   4649.714278    37765
317      AL                Cullman County   5213.714278    80406
332      AL                   Dale County   4805.714278    50251
347      AL                 Dallas County   5081.714278    43820
362      AL                 DeKalb County   4637.714278    71109
377      AL                 Elmore County   7145.714278    79303
392      AL               Escambia County   5381.714278    38319
407      AL                 Etowah County   4793.714278   104430
437      AL               Franklin County   5309.714278    31704
452      AL                 Geneva County   5021.714278    26790
512      AL                Houston County   5021.714278   101547
527      AL                Jackson County   5705.714278    53227
542      AL              Jefferson County   7949.714278   658466
572      AL             Lauderdale County   5201.714278    92709
587      AL               Lawrence County   5129.714278    34339
602      AL                    Lee County   6317.714278   140247
617      AL              Limestone County   7013.714278    82782
662      AL                Madison County   7013.714278   334811
692      AL                 Marion County   4493.714278    30776
707      AL               Marshall County   4625.714278    93019
722      AL                 Mobile County   6965.714278   412992
752      AL             Montgomery County   7145.714278   229363
767      AL                 Morgan County   5129.714278   119490
812      AL                   Pike County   5273.714278    32899
842      AL                Russell County   7361.714278    52947
872      AL                 Shelby County   7949.714278   195085
857      AL              St. Clair County   7949.714278    83593
902      AL              Talladega County   4889.714278    82291
917      AL             Tallapoosa County   5261.714278    41616
932      AL             Tuscaloosa County   7253.714278   194656
947      AL                 Walker County   4817.714278    67023
1697     AR                 Baxter County   5285.714278    41513
1712     AR                 Benton County   5825.714278   221339
1727     AR                  Boone County   4697.714278    36903
1772     AR                Carroll County   4781.714278    27446
1832     AR               Cleburne County   5141.714278    25970
1892     AR              Craighead County   6101.714278    96443
1907     AR               Crawford County   5141.714278    61948
1922     AR             Crittenden County   7697.714278    50902
1997     AR               Faulkner County   7217.714278   113237
2042     AR                Garland County   5837.714278    96024
2072     AR                 Greene County   5849.714278    42090
2102     AR             Hot Spring County   5273.714278    32923
2132     AR           Independence County   4685.714278    36647
2177     AR              Jefferson County

In [77]:
col_rent.to_csv("./dataframes/col_rent.csv")